## Water Productivity assessment
#### Download and process Level 3 data from WaPOR - Gezira Irrigation Scheme

Notebook prepared by Ben Maathuis, Bas Retsios and Willem Nieuwenhuis. ITC-University of Twente, Enschede. The Netherlands

Making use of WAPOR-DL (https://bitbucket.org/cioapps/wapordl/src/main/)

WaPOR data needed for Water Productivity assessment will be downloaded and processed for a part of the Gezira Scheme in Sudan for which Level 3 data is available. The crop selected is sorghum and the crop mask extraction is based on the information acquired during a field survey which was conducted in 2019. The sorghum crop mask will be extracted using some general assumptions based on the field experiences gained.

AETI, T and NPP data is downloaded from the WaPOR data repository (using WAPOR-DL) and is converted to the correct unit, aggregated over the crop growing season and Land (biomass and crop yield) and (gross and net) Water Productivity is assessed, followed by some other irrigation performance indicators like Uniformity, Beneficial fraction and Relative Water Deficit. The formula's applied are derived from the Water Productivity in Practice Project (Water-PIP).

All data is stored locally (under the notebook folder) and is available in Ilwis raster format. ILWIS386 can be used for visualization and the latest version can be downloaded from: https://filetransfer.itc.nl/pub/52n/ILWIS386/Software/.  The installation manual is available from: https://filetransfer.itc.nl/pub/52n/ILWIS386/Tutorial/

In the Gezira Irrigation Scheme, the average sorghum yield is estimated to be around 1.212 tons per hectare (ha). Studies suggest that this yield can be significantly higher, reaching a potential yield of 2000-4000 kg/ha. Furthermore some reference figures from different sources:

+ The Gezira scheme's sorghum crop experiences an average seasonal transpiration of 322 mm and an average seasonal evapotranspiration of 496 mm. 
+ The average seasonal gross crop water productivity for sorghum is 0.43 kg/m3. 
+ The scheme's sorghum yield can vary significantly across different locations, with El Naseeh block in the middle of the Managil major canal showing a yield of 1.212 tons/ha.

Challenges:
The Gezira scheme has faced challenges like low productivity, poor water management, and irrigation mismanagement. A steady decline in sorghum yield was observed since the 1970s, with yields decreasing from 744.3 kg/ha to 476.6 kg/ha since 1982. 

Some further information can be obtained from:
+ https://www.researchgate.net/publication/299061128_Remote_Sensing_Derived_Crop_Coefficient_for_Estimating_Crop_Water_Requirements_for_Irrigated_Sorghum_in_the_Gezira_Scheme_Sudan
+ https://www.mdpi.com/2073-4395/15/1/110
+ https://github.com/eLEAF-Github/WAPORACT Water Productivity in Practice project (WaterPIP)

In [ ]:
#if WaPOR-DL is not installed uncomment the line below and execute this field
#!pip install wapordl

In [ ]:
#load libraries
import wapordl
import matplotlib.pyplot as plt
from matplotlib.colors import ListedColormap, BoundaryNorm
from IPython.display import HTML
from datetime import datetime, timedelta
import ilwis
import numpy as np
import sys
import os
import glob
import warnings

#### Get some general information on WaPOR level 3 areas and level 1, 2 and 3 variables

In [ ]:
#uncomment the line below to get a listing of the level 3 areas
#here we will use the data from: 'GEZ': 'Gezira, Sudan'
wapordl.region_selector.l3_codes()

In [ ]:
#uncomment the line below to get a listing of the level 1, 2 and 3 variables
#here we use level 3
wapordl.variable_descriptions.WAPOR3_VARS

### Season for Sorghum
+ SOS = dekad 3 July
+ EOS = dekad 3 November

Specify the year to be selected in the field below.

In [ ]:
year = '2020'

In [ ]:
#create a few folders to store the data downloaded / processed
folder = os.getcwd()+r'/waporl3_download'
os.chdir(".")
print("current dir is: %s" % (os.getcwd()))

if os.path.isdir(folder):
    print("Folder exists")
else:
    print("Folder doesn't exists")
    os.mkdir(folder)

In [ ]:
#create a few folders to store the data downloaded / processed
folder = os.getcwd()+ r'/waporl3_'+year
os.chdir(".")
print("current dir is: %s" % (os.getcwd()))

if os.path.isdir(folder):
    print("Folder exists")
else:
    print("Folder doesn't exists")
    os.mkdir(folder)

In [ ]:
#set sample data folder
#use the Python function os.getcwd() to retrieve the current folder used and add the apporriate sub-folder
download_dir = os.getcwd() + r'/waporl3_download'
working_dir = os.getcwd() +r'/waporl3_'+year

#set the working directory for ILWISPy
ilwis.setWorkingCatalog(working_dir)
print(ilwis.version())
print(download_dir)
print(working_dir)

### Retrieve time series data for AETI, NPP and T

#### Retrieve and process AETI

In [ ]:
region = "GEZ"
folder = download_dir
variable = "L3-AETI-D"
period = [year+"-07-21", year+"-11-21"]
unit = "dekad" # or choose "day", "month", "year", "none" (default).
overview = -1 #or "None"

aeti_df = wapordl.wapor_ts(region, variable, period, overview=overview, unit_conversion=unit)
aeti_fp = wapordl.wapor_map(region, variable, period, folder, overview=overview, unit_conversion=unit)

In [ ]:
aeti_df

In [ ]:
aeti_df.attrs

In [ ]:
aeti_fp

In [ ]:
# rename downloaded file
old_aeti = aeti_fp
new_aeti = download_dir+ '/GEZ_L3-AETI-D_NONE_dekad_converted_'+year+'.tif'

# Rename the file
os.rename(old_aeti, new_aeti)

In [ ]:
ilwis.setWorkingCatalog(working_dir)
print(working_dir)

In [ ]:
aeti_ds = ilwis.RasterCoverage(new_aeti)

In [ ]:
#check meta data
print(aeti_ds.size())
print(aeti_ds.envelope())
coordSys = aeti_ds.coordinateSystem()
coordSys.toWKT()

In [ ]:
#Note pandas df for date of rasterband selected (2021-09-11	2021-09-20)
ts1 = ilwis.do('selection',aeti_ds,"rasterbands(5)")
ts1 = ilwis.do('mapcalc', 'iff(@1==?, -10, @1*0.1)',ts1) #*apply scaling, see also max of layer 05!

In [ ]:
ts_2np = np.fromiter(iter(ts1), np.float64, ts1.size().linearSize()) 
ts_2np = ts_2np.reshape((ts1.size().ysize, ts1.size().xsize))

In [ ]:
min_val = np.nanmin(ts_2np)
max_val = np.nanmax(ts_2np)
print(min_val)
print(max_val)

In [ ]:
# Create custom colormap

cmap = plt.cm.jet
cmap_colors = cmap(np.linspace(0, 1, 256))

# Add white at the beginning for the -1 value
new_colors = np.vstack(([1, 1, 1, 1], cmap_colors))
new_cmap = ListedColormap(new_colors)

# Create bounds and norm
max_val = np.nanmax(ts_2np[ts_2np >= 0])  # Ignore -1 in max calc
bounds = np.linspace(0, max_val, num=258)  # One extra bin for -1
norm = BoundaryNorm(boundaries=bounds, ncolors=new_cmap.N)

# Plot
plt.imshow(ts_2np, cmap=new_cmap, norm=norm)
plt.colorbar(label='Data Value', shrink=0.5)
#plt.title('Custom Colormap with -1 as White')
plt.title('AETI-ts05 (mm/dek)')
plt.show()

In [ ]:
ts_aeti = ilwis.do('mapcalc', 'iff(@1==?,-10, @1*0.1)',aeti_ds) #set background to value of -10 and apply scaling factor to all layers
ts_aeti.store('gez_aeti.mpl')

#### Retrieve and process NPP

In [ ]:
region = "GEZ"
folder = download_dir
variable = "L3-NPP-D"
period = [year+"-07-21", year+"-11-21"]
overview = -1 #or "None"
unit = "dekad" # or choose "day", "month", "year", "none" (default).

npp_df = wapordl.wapor_ts(region, variable, period, overview=overview, unit_conversion=unit)
npp_fp = wapordl.wapor_map(region, variable, period, folder, unit_conversion=unit)

In [ ]:
npp_df.attrs

In [ ]:
npp_df

In [ ]:
npp_fp

In [ ]:
# rename downloaded file
old_npp = npp_fp
new_npp = download_dir+ '/GEZ_L3-NPP-D_NONE_dekad_converted_'+year+'.tif'

# Rename the file
os.rename(old_npp, new_npp)

In [ ]:
npp_ds = ilwis.RasterCoverage(new_npp)

In [ ]:
#Note rasterband time step selected (2021-09-11	2021-09-20)
ts2 = ilwis.do('selection',npp_ds,"rasterbands(5)")
ts2 = ilwis.do('mapcalc', 'iff(@1==?, -10, @1*0.001)',ts2) #apply scaling factor, see max of layer 05!

In [ ]:
ts_2np = np.fromiter(iter(ts2), np.float64, ts2.size().linearSize()) 
ts_2np = ts_2np.reshape((ts2.size().ysize, ts2.size().xsize))

In [ ]:
min_val = np.nanmin(ts_2np)
max_val = np.nanmax(ts_2np)
print(min_val)
print(max_val)

In [ ]:
# Create custom colormap

cmap = plt.cm.jet
cmap_colors = cmap(np.linspace(0, 1, 256))

# Add white at the beginning for the -1 value
new_colors = np.vstack(([1, 1, 1, 1], cmap_colors))
new_cmap = ListedColormap(new_colors)

# Create bounds and norm
max_val = np.nanmax(ts_2np[ts_2np >= 0])  # Ignore -1 in max calc
bounds = np.linspace(0, max_val, num=258)  # One extra bin for -1
norm = BoundaryNorm(boundaries=bounds, ncolors=new_cmap.N)

# Plot
plt.imshow(ts_2np, cmap=new_cmap, norm=norm)
plt.colorbar(label='Data Value', shrink=0.5)
#plt.title('Custom Colormap with -1 as White')
plt.title('NPP-ts05 (gC/m2/dek)')
plt.show()

In [ ]:
ts_npp = ilwis.do('mapcalc', 'iff(@1==?, -10, @1*0.001)',npp_ds) #set background to value of -10 and apply scaling factor to all layers
ts_npp.store('gez_npp.mpl')

#### Retrieve and process T

In [ ]:
region = "GEZ"
folder = download_dir
variable = "L3-T-D"
period = [year+"-07-21", year+"-11-21"]
overview = -1 #or "None"
unit = "dekad" # or choose "day", "month", "year", "none" (default).

t_df = wapordl.wapor_ts(region, variable, period, overview=overview, unit_conversion=unit)
t_fp = wapordl.wapor_map(region, variable, period, folder, overview=overview, unit_conversion=unit)

In [ ]:
t_df.attrs

In [ ]:
t_df

In [ ]:
t_fp

In [ ]:
# rename downloaded file
old_t = t_fp
new_t = download_dir+ '/GEZ_L3-T-D_NONE_dekad_converted_'+year+'.tif'

# Rename the file
os.rename(old_t, new_t)

In [ ]:
t_ds = ilwis.RasterCoverage(new_t)

In [ ]:
#Note rasterband time step selected (2021-09-01	2021-09-10)
ts7 = ilwis.do('selection',t_ds,"rasterbands(7)")
ts7 = ilwis.do('mapcalc', 'iff(@1==?, -10, @1*0.1)',ts7) #apply scaling factor, see max of layer 05!

In [ ]:
ts_2np = np.fromiter(iter(ts7), np.float64, ts7.size().linearSize()) 
ts_2np = ts_2np.reshape((ts7.size().ysize, ts7.size().xsize))

In [ ]:
min_val = np.nanmin(ts_2np)
max_val = np.nanmax(ts_2np)
print(min_val)
print(max_val)

In [ ]:
# Create custom colormap

cmap = plt.cm.jet
cmap_colors = cmap(np.linspace(0, 1, 256))

# Add white at the beginning for the -1 value
new_colors = np.vstack(([1, 1, 1, 1], cmap_colors))
new_cmap = ListedColormap(new_colors)

# Create bounds and norm
max_val = np.nanmax(ts_2np[ts_2np >= 0])  # Ignore -1 in max calc
bounds = np.linspace(0, max_val, num=258)  # One extra bin for -1
norm = BoundaryNorm(boundaries=bounds, ncolors=new_cmap.N)

# Plot
plt.imshow(ts_2np, cmap=new_cmap, norm=norm)
plt.colorbar(label='Data Value', shrink=0.5)
#plt.title('Custom Colormap with -1 as White')
plt.title('T-ts07 (mm/dek)')
plt.show()

In [ ]:
ts_t = ilwis.do('mapcalc', 'iff(@1==?, -10, @1*0.1)',t_ds) #set background to value of -10 and apply scaling factor to all layers
ts_t.store('gez_t.mpl')

### Aggregate timeseries of AETI, NPP and T to season sum

In [ ]:
AETI_Season = ilwis.do('aggregaterasterstatistics', ts_aeti, 'sum')
AETI_Season.store('aeti_sum.mpr') # mm/season

In [ ]:
NPP_Season = ilwis.do('aggregaterasterstatistics', ts_npp, 'sum')
NPP_Season.store('npp_sum.mpr') #gC/m2/season

In [ ]:
T_Season = ilwis.do('aggregaterasterstatistics', ts_t, 'sum')
T_Season.store('t_sum.mpr') # mm/season

### Create a Sorghum crop mask
Next to Sorghum other main crops are cotton, groundnut, pigeonpea and onion. Also there is wide range of other crops cultivated but in small areas such as okra, cowpea, sesame and white bean among others. Sorghum is planted in (mid-end) July and harvested in (end) November, which is destinctively different from the other main crops. To approximate the sorghum crop cycle from the Transpiration time series from the mid-season a minimum and maximum transpiration threshold (20 mm/dek / 70 mm/dek) is expected, at the start of the season - initial stage an increase in transpiration, from mid-season towards end of season a decrease in Transpiration and during the late season Transpiration is less than 20 mm/dek.

In [ ]:
#selection of timesteps to be used in the sorghum crop mask creation (from Transpiration cycle)
t1= ilwis.do('selection',ts_t,"rasterbands(0")
t2= ilwis.do('selection',ts_t,"rasterbands(1)")
t3= ilwis.do('selection',ts_t,"rasterbands(2)")
t4= ilwis.do('selection',ts_t,"rasterbands(3)")
t5= ilwis.do('selection',ts_t,"rasterbands(4)")
t6= ilwis.do('selection',ts_t,"rasterbands(5)")
t7= ilwis.do('selection',ts_t,"rasterbands(6)")
t8= ilwis.do('selection',ts_t,"rasterbands(7)")
t9= ilwis.do('selection',ts_t,"rasterbands(8)")
t10= ilwis.do('selection',ts_t,"rasterbands(9)")
t11= ilwis.do('selection',ts_t,"rasterbands(10)")
t12= ilwis.do('selection',ts_t,"rasterbands(11)")
t13= ilwis.do('selection',ts_t,"rasterbands(12)")

Creating a Sorghum crop mask using the individual Transpiration layers selected

In [ ]:
mask_season = ilwis.do('mapcalc', 'iff((@1>250)and(@1<400),1,0)',T_Season)# using season mask to differentiate from cotton which is having overall 
#seasonal higher Transpiration rates, and from groundnut, pigeonpea or onion which are having lower Transpiration rates

mask_th = ilwis.do('mapcalc', 'iff((@1>25)and(@1<70),1,0)',t7) #threshold on maximum mid-season T, to differentiate from cotton which is having higher 
#Transpiration rates during mid-season, and from groundnut, pigeonpea or onion which are having lower mid-season Transpiration rates

mask_up = ilwis.do('mapcalc', 'iff((@1<@2)and(@3<@4),1,0)',t2,t3,t6,t7) #increase in T from initial through development stage

mask_down = ilwis.do('mapcalc', 'iff((@2<@1),1,0)',t10,t11) #decrease in T in late season stage

mask_end = ilwis.do('mapcalc', 'iff(@1<20,1,0)',t13) #hardly any T during late - end of season stage

#extract the final sorghum mask - should meet all above consitions
mask = ilwis.do('mapcalc', 'iff(@1+@2+@3+@4+@5==5,1,0)',mask_season,mask_th,mask_up,mask_down,mask_end)
mask.store('sorghum_mask_'+year+'.mpr')

### Calculate land productivity (LP)

Following crop parameters for Sorghum are used:
+ Harvest Index (HI) = 0.25
+ Above ground over total biomass (AOT) = 0.8 # above ground over total biomass production ratio
+ Moisture Content (MC) = 0.2  # moisture content, dry matter over freshbiomass
+ Light use efficiency correction factor (fc) = 1.6  # Light use efficiency correction factor for C4 crops


AGBM = (AOT * fc * (NPP * 22.222 / (1 - MC))) / 1000  # factor of 1000 is to convert from kg to ton 

where  AGMB is the above ground biomass, AOT is the above ground over total biomass production fraction, fc is the light use efficiency correction factor, NPP is seasonal net primary production in gC/m²/season, MC is moisture content in the fresh biomass 


to calculate crop yield:    Crop yield = HI*AGBM

where HI is harvest index, and AGBM is above ground biomass

In [ ]:
AGBM = ilwis.do('mapcalc', '(0.8*1.6*(@1*22.222/(1-0.2)))/1000',NPP_Season) #convert from kg to ton
AGBM_sorghum = ilwis.do('mapcalc', 'iff(@1=1,@2,?)',mask, AGBM) 

In [ ]:
Yield = ilwis.do('mapcalc', '(0.25*@1)',AGBM) 
Yield_sorghum = ilwis.do('mapcalc', 'iff(@1=1,@2,?)',mask, Yield) 

In [ ]:
AGBM_sorghum.store('agbm_sorghum.mpr') #tons/ha/season
Yield_sorghum.store('yield_sorghum_'+year+'.mpr') #tons/ha/season

In [ ]:
#Get statistics and plot graph
def descriptive_statistics(raster_input):
    stats_input = raster_input.statistics(ilwis.PropertySets.pHISTOGRAM)
    print()
    print('Minimum: ',stats_input[ilwis.PropertySets.pMIN]) 
    print('Maximum: ',stats_input[ilwis.PropertySets.pMAX]) 
    print('Mean: ',stats_input[ilwis.PropertySets.pMEAN]) 
    print()
    x=[a for (a,b) in stats_input.histogram()][:-1] 
    y=[b for (a,b) in stats_input.histogram()][:-1]
    plt.figure(figsize=(4, 4))
    plt.plot(x,y,label='Map values')
    plt.xlabel('Data Range')
    plt.ylabel('Data Frequency')
    plt.title('Map Histogram')
    plt.legend()

In [ ]:
descriptive_statistics(AGBM_sorghum)

In [ ]:
descriptive_statistics(Yield_sorghum)

### Calculate gross and net water productivity (WP)

#### Calculate gross , net biomass and crop yield water productivity 
To calculate Gross Biomass Water Productivity: WPg_biomass = Biomass / AETI *100     

where Biomass = seasonal AGBM and AETI = seasonal AETI

To calculate Net Biomass Water Productivity: WPn_biomass = Biomass / T *100   

where Biomass = seasonal AGBM and T = seasonal Transpitation #fraction beneficially consumed by the crop

In [ ]:
WPg_biomass = ilwis.do('mapcalc', '(@1/@2*100)',AGBM, AETI_Season) # for kg/m3
WPg_biomass = ilwis.do('mapcalc', 'iff(@1=1,@2,?)',mask, WPg_biomass) 

In [ ]:
WPg_biomass.store('WPg_biomass_sorghum.mpr')

In [ ]:
descriptive_statistics(WPg_biomass)

In [ ]:
WPn_biomass = ilwis.do('mapcalc', '(@1/@2*100)',AGBM, T_Season) # for kg/m3
WPn_biomass = ilwis.do('mapcalc', 'iff(@1=1,@2,?)',mask, WPn_biomass) 

In [ ]:
WPn_biomass.store('WPn_biomass_sorghum_'+year+'.mpr')

In [ ]:
descriptive_statistics(WPn_biomass)

To calculate Crop Yield Water Productivity: Yield WP = Yield / AETI *100      
where Biomass = seasonal Yield and AETI = seasonal AETI

In [ ]:
WPyield = ilwis.do('mapcalc', '(@1/@2*100)',Yield, AETI_Season) # for kg/m3
WPyield = ilwis.do('mapcalc', 'iff(@1=1,@2,?)',mask, WPyield) 

In [ ]:
WPyield.store('WPyield_sorghum_'+year+'.mpr')

In [ ]:
descriptive_statistics(WPyield)

### Calculate some other performance indicators

#### Uniformity of water consumption
Equity is defined as the coefficients of variation (CV) of seasonal AETI in the area of interest. It measures the evenness of the water supply in an irrigation scheme. It is defined as:   CV_AETI = (AETIsd / AETIm) * 100

where:
+ AETIsd = standard deviation
+ AETIm = mean

CV classification, according to Bastiaanssen et al., 1996): 
+ CV of 0 to 10% is good
+ CV of 10 to 25% is fair 
+ CV > 25% is poor uniformity

In [ ]:
#transform ilwis raster to numpy array 
AETI_np = np.fromiter(iter(AETI_Season), np.float64, AETI_Season.size().linearSize()) #transform to 1D array
AETI_np = AETI_np.reshape((AETI_Season.size().ysize, AETI_Season.size().xsize))

#assign background value of -130 to np.nan
AETI_np[AETI_np == -130] = np.nan 

pmean_a = np.nanmean(AETI_np)
pstdev_a = np.nanstd(AETI_np)

print('mean =', pmean_a) # mean value
print('std =', pstdev_a) #std value

In [ ]:
CV_AETI_wholescheme = (pstdev_a/pmean_a) * 100
print('CV of the whole scheme (%) = ', CV_AETI_wholescheme)

In [ ]:
#set background to -130 and transform ilwis raster to numpy array for sorghum only
CV_AETI_sorghum_2np = ilwis.do('mapcalc', 'iff(@1==1,@2,-130)', mask, AETI_Season) 
#CV_AETI_sorghum_2np.store('CV_AETI_sorghum_2np.mpr')

AETI_np = np.fromiter(iter(CV_AETI_sorghum_2np), np.float64, CV_AETI_sorghum_2np.size().linearSize()) #transform to 1D array
AETI_np = AETI_np.reshape((CV_AETI_sorghum_2np.size().ysize, CV_AETI_sorghum_2np.size().xsize))

#assign background value of -130 to np.nan
AETI_np[AETI_np == -130] = np.nan 

pmean_s = np.nanmean(AETI_np)
pstdev_s = np.nanstd(AETI_np)

print('mean =', pmean_s) # mean value
print('std =', pstdev_s) #std value

In [ ]:
CV_AETI_sorghum = (pstdev_s/pmean_s) * 100
print('CV of sorghum in the scheme (%) = ',CV_AETI_sorghum)

#### Calculate Beneficial Fraction (BF)

Beneficial fraction is the ratio of the water that is consumed as transpiration (T) compared to overall field water consumption (AETI).  
It is a measure of the efficiency of on farm water and agronomic practices in use of water for crop growth.

It is defined as: BF = T/AETI

In [ ]:
BF_scheme = ilwis.do('mapcalc', 'iff(@1>=0,@1/@2,?)',T_Season, AETI_Season)
BF_scheme.store('BF_scheme.mpr')

In [ ]:
BF_sorghum = ilwis.do('mapcalc', 'iff(@1==1,@2/@3,?)',mask,T_Season, AETI_Season)
BF_sorghum.store('BF_sorghum.mpr')

In [ ]:
descriptive_statistics(BF_sorghum)

#### Calculate Relative Water Deficit (RWD)

Relative water deficit = ETa / ETx

ETx = 99 percentile of the actual evapotranspiration


In [ ]:
#transform from ilwis raster to numpy array whole scheme
AETI_np = np.fromiter(iter(AETI_Season), np.float64, AETI_Season.size().linearSize()) #transform to 1D array

#assign -130 to np.nan
AETI_np[AETI_np==-130]=np.nan

ETx = np.nanpercentile(AETI_np, 99)
AETI_mean = pmean_a
RWD = 1-(AETI_mean/ETx)

print('ETx = ',ETx)
print('AETI_mean = ',AETI_mean)
print('RWD = ',RWD)

In [ ]:
#transform from ilwis raster to numpy array sorghum only
AETI_np = np.fromiter(iter(CV_AETI_sorghum_2np), np.float64, CV_AETI_sorghum_2np.size().linearSize()) #transform to 1D array

#assign -130 to np.nan
AETI_np[AETI_np==-130]=np.nan

ETx = np.nanpercentile(AETI_np, 99)
AETI_mean = pmean_s
RWD = 1-(AETI_mean/ETx)

print('ETx = ',ETx)
print('AETI_mean = ',AETI_mean)
print('RWD = ',RWD)

#### Eventually process another year and compare it with the results obtained for 2020